# Cleaning Data

In [1]:
import pandas as pd
import numpy as np

Load Dataset

In [2]:
player = 'cole'
data = pd.read_csv('./data/' + player + '.csv')
print(data)

       Unnamed: 0 pitch_type   game_date  release_speed  release_pos_x  \
0               0         KC  2018-10-14           80.6          -2.04   
1               1         SL  2018-10-14           88.0          -2.01   
2               2         CH  2018-10-14           86.1          -2.23   
3               3         CH  2018-10-14           87.5          -2.14   
4               4         KC  2018-10-14           80.5          -2.04   
...           ...        ...         ...            ...            ...   
21489        5407         SL  2019-03-29           89.8          -2.35   
21490        5408         FF  2019-03-29           96.3          -2.16   
21491        5409         SL  2019-03-29           88.5          -2.34   
21492        5410         FT  2019-03-29           96.7          -2.34   
21493        5411         FF  2019-03-29           96.2          -2.24   

       release_pos_z   player_name  batter  pitcher     events  ... fld_score  \
0               5.61  Cole, Ge

/home/logan/.local/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3165: DtypeWarning: Columns (44) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


Simplify the batters on base columns:

In [3]:
data['on_base'] = np.sum([
    pd.notnull(data['on_1b']),
    pd.notnull(data['on_2b']),
    pd.notnull(data['on_3b'])
], axis=0)

print(data)

       Unnamed: 0 pitch_type   game_date  release_speed  release_pos_x  \
0               0         KC  2018-10-14           80.6          -2.04   
1               1         SL  2018-10-14           88.0          -2.01   
2               2         CH  2018-10-14           86.1          -2.23   
3               3         CH  2018-10-14           87.5          -2.14   
4               4         KC  2018-10-14           80.5          -2.04   
...           ...        ...         ...            ...            ...   
21489        5407         SL  2019-03-29           89.8          -2.35   
21490        5408         FF  2019-03-29           96.3          -2.16   
21491        5409         SL  2019-03-29           88.5          -2.34   
21492        5410         FT  2019-03-29           96.7          -2.34   
21493        5411         FF  2019-03-29           96.2          -2.24   

       release_pos_z   player_name  batter  pitcher     events  ...  \
0               5.61  Cole, Gerrit  5438

Now, we explicitly list the columns that we want to keep:

In [4]:
keep_columns = [
    'pitch_type',
    'game_date',
    'release_speed',
    'batter',
    'events',
    'zone',
    'stand',
    'type',
    'bb_type',
    'balls',
    'strikes',
    'plate_x',
    'plate_y',
    'plate_z',
    'outs_when_up',
    'inning',
    'game_pk',
    'pitch_num',
    'pitch_name',
    'home_score',
    'away_score',
    'bat_score',
    'fld_score',
    'on_base'
]

Delete the unnecessary columns:

In [5]:
for column in data:
    if column not in keep_columns:
        data.pop(column)

print("Kept Columns:")
for column in data:
    print(column)

Kept Columns:
pitch_type
game_date
release_speed
batter
events
zone
stand
type
bb_type
balls
strikes
plate_x
plate_z
outs_when_up
inning
game_pk
pitch_name
home_score
away_score
bat_score
fld_score
on_base


In the data we have, the pitch (label) and the results of the pitch are in the same row. We would like the label to be on the same row as the previous pitch data, so we need to shift some of the columns down one row. 

In [6]:
to_shift_down = [
    'events',
    'zone',
    'type',
    'bb_type',
    'plate_x',
    'plate_z'
]

groups = data.groupby(['game_pk', 'inning'])

list_of_dfs = []
for _, g in groups:
    list_of_dfs.append(g)

print(list_of_dfs)

for df in list_of_dfs:
    for column in df:
        if column in to_shift_down:
            data[column].shift(1)
            
cleaned_data = pd.concat(list_of_dfs, axis=0, sort=False)
    
# size = len(data[column])
# print(size)

# for column in data:
#     if column in to_shift_down:
#         data[column].shift(1)
                
# for column in data:
#     if column in to_shift_down:
#         for i, row in enumerate(data[column]):
#             if i != 0 and i < size - 2:
#                 if (data['game_pk'][i] != data['game_pk'][i-1]) or (data['inning'][i] != data['inning'][i-1]):
#                     data.loc[column, i] = np.NaN

[      pitch_type   game_date  release_speed  batter     events  zone stand  \
16064         FF  2013-06-11           97.7  474832  field_out   6.0     L   
16065         FF  2013-06-11           99.6  474832        NaN  12.0     L   
16066         SI  2013-06-11           97.4  474832        NaN   5.0     L   
16067         FF  2013-06-11           97.9  474832        NaN  14.0     L   
16068         FF  2013-06-11           98.7  474832        NaN  14.0     L   
16069         FF  2013-06-11           97.4  452254     single   5.0     R   
16070         SL  2013-06-11           86.0  452254        NaN  14.0     R   
16071         SI  2013-06-11           97.6  452254        NaN   7.0     R   
16072         FF  2013-06-11           97.2  452254        NaN   6.0     R   
16073         CH  2013-06-11           87.5  457763  field_out   4.0     R   
16074         FF  2013-06-11           96.4  457763        NaN   8.0     R   
16075         FF  2013-06-11           96.5  457763        NaN 

Save the data:

In [7]:
cleaned_data.to_csv('./cleaned_data/' + player + '.csv')